In [2]:
import pandas as pd
from sqlalchemy import create_engine
import json
from transformers import AutoTokenizer, AutoModel
import torch

d:\Dev\Project\VN-Law\chat-service\.venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [6]:

DB_USER = 'root'
DB_PASSWORD = 'password'
DB_HOST = 'localhost'
DB_PORT = 4000  # Add the port number
DB_NAME ='law_service'

# Creating the connection
engine = create_engine(f'mysql+mysqlconnector://{DB_USER}:{DB_PASSWORD}@{DB_HOST}:{DB_PORT}/{DB_NAME}')


print("Connection established")

Connection established


In [7]:
query = """
SELECT 
    pdtopic.id AS topic_id,
    pdtopic.name AS topic_name,
    pdsubject.id AS subject_id,
    pdsubject.name AS subject_name,
    pdchapter.id AS chapter_id,
    pdchapter.name AS chapter_name,
    pdarticle.id AS article_id,
    pdarticle.content AS article_content
FROM 
    pdtopic
JOIN 
    pdsubject ON pdsubject.id_topic = pdtopic.id
JOIN 
    pdchapter ON pdchapter.id_subject = pdsubject.id
JOIN 
    pdarticle ON pdarticle.id_chapter = pdchapter.id
ORDER BY 
    pdtopic.id, pdsubject.id, pdchapter.id, pdarticle.id;
"""

data = pd.read_sql(query, engine)

print(data.head())
print("Data fetched")

                               topic_id         topic_name  \
0  01684735-cbae-4b6f-9471-1010ab2f350a  Tương trợ tư pháp   
1  01684735-cbae-4b6f-9471-1010ab2f350a  Tương trợ tư pháp   
2  01684735-cbae-4b6f-9471-1010ab2f350a  Tương trợ tư pháp   
3  01684735-cbae-4b6f-9471-1010ab2f350a  Tương trợ tư pháp   
4  01684735-cbae-4b6f-9471-1010ab2f350a  Tương trợ tư pháp   

                             subject_id       subject_name  \
0  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  Tương trợ tư pháp   
1  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  Tương trợ tư pháp   
2  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  Tương trợ tư pháp   
3  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  Tương trợ tư pháp   
4  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  Tương trợ tư pháp   

             chapter_id                   chapter_name  \
0  40001000000000001000  Chương I NHỮNG QUY ĐỊNH CHUNG   
1  40001000000000001000  Chương I NHỮNG QUY ĐỊNH CHUNG   
2  40001000000000001000  Chương I NHỮNG QUY ĐỊNH CHUNG   
3  4000100000000000100

In [8]:
data = data.dropna(subset=['topic_name', 'subject_name', 'chapter_name', 'article_content'])
data = data.drop_duplicates(subset=['topic_name', 'subject_name', 'chapter_name', 'article_content'])
data['topic_name'] = data['topic_name'].str.lower()
data['subject_name'] = data['subject_name'].str.lower()
data['chapter_name'] = data['chapter_name'].str.lower()
data['article_content'] = data['article_content'].str.lower()
data['article_content'] = data['article_content'].str.replace(r'[^\w\s]', '', regex=True)
data['article_content'] = data['article_content'].str.replace(r'\s+', ' ', regex=True).str.strip()


print(data.head())

                               topic_id         topic_name  \
0  01684735-cbae-4b6f-9471-1010ab2f350a  tương trợ tư pháp   
1  01684735-cbae-4b6f-9471-1010ab2f350a  tương trợ tư pháp   
2  01684735-cbae-4b6f-9471-1010ab2f350a  tương trợ tư pháp   
3  01684735-cbae-4b6f-9471-1010ab2f350a  tương trợ tư pháp   
4  01684735-cbae-4b6f-9471-1010ab2f350a  tương trợ tư pháp   

                             subject_id       subject_name  \
0  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  tương trợ tư pháp   
1  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  tương trợ tư pháp   
2  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  tương trợ tư pháp   
3  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  tương trợ tư pháp   
4  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  tương trợ tư pháp   

             chapter_id                   chapter_name  \
0  40001000000000001000  chương i những quy định chung   
1  40001000000000001000  chương i những quy định chung   
2  40001000000000001000  chương i những quy định chung   
3  4000100000000000100

In [9]:
data['combined_data'] = (
    "Topic: " + data['topic_name'] + "\n" +
    "Subject: " + data['subject_name'] + "\n" +
    "Chapter: " + data['chapter_name'] + "\n" +
    "Article: " + data['article_content']
)

print(data.head())

                               topic_id         topic_name  \
0  01684735-cbae-4b6f-9471-1010ab2f350a  tương trợ tư pháp   
1  01684735-cbae-4b6f-9471-1010ab2f350a  tương trợ tư pháp   
2  01684735-cbae-4b6f-9471-1010ab2f350a  tương trợ tư pháp   
3  01684735-cbae-4b6f-9471-1010ab2f350a  tương trợ tư pháp   
4  01684735-cbae-4b6f-9471-1010ab2f350a  tương trợ tư pháp   

                             subject_id       subject_name  \
0  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  tương trợ tư pháp   
1  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  tương trợ tư pháp   
2  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  tương trợ tư pháp   
3  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  tương trợ tư pháp   
4  e8e1515c-249d-4a9b-af30-ac0d8a3aac7d  tương trợ tư pháp   

             chapter_id                   chapter_name  \
0  40001000000000001000  chương i những quy định chung   
1  40001000000000001000  chương i những quy định chung   
2  40001000000000001000  chương i những quy định chung   
3  4000100000000000100

In [ ]:


data[['topic_name', 'subject_name', 'chapter_name', 'article_content', 'combined_data']].to_json("data/combined_data.json", orient="records", lines=True)
data[['topic_name', 'subject_name', 'chapter_name', 'article_content', 'combined_data']].to_csv("data/combined_data.csv", index=False)

print("Data saved")

Data saved


In [18]:
df = pd.read_json("combined_data.json", orient="records", lines=True)
print(df.head())

          topic_name       subject_name                   chapter_name  \
0  tương trợ tư pháp  tương trợ tư pháp  chương i những quy định chung   
1  tương trợ tư pháp  tương trợ tư pháp  chương i những quy định chung   
2  tương trợ tư pháp  tương trợ tư pháp  chương i những quy định chung   
3  tương trợ tư pháp  tương trợ tư pháp  chương i những quy định chung   
4  tương trợ tư pháp  tương trợ tư pháp  chương i những quy định chung   

                                     article_content  \
0  luật này quy định nguyên tắc thẩm quyền trình ...   
1  luật này áp dụng đối với cơ quan tổ chức cá nh...   
2  1 tương trợ tư pháp được thực hiện theo quy đị...   
3  1 pháp luật nước ngoài được áp dụng theo quy đ...   
4  nghị định này quy định chi tiết và hướng dẫn t...   

                                       combined_data  
0  Topic: tương trợ tư pháp\nSubject: tương trợ t...  
1  Topic: tương trợ tư pháp\nSubject: tương trợ t...  
2  Topic: tương trợ tư pháp\nSubject: tương trợ t... 

In [11]:
# Cell 1: Import các thư viện cần thiết
from sqlalchemy import create_engine
import mysql.connector
from mysql.connector import Error
import pandas as pd

# Cell 2: Thiết lập thông tin kết nối
DB_USER = 'root'
DB_PASSWORD = 'password'
DB_HOST = 'localhost'
DB_PORT = 4000
DB_NAME = 'chat_service'

# Cell 3: Hàm kiểm tra và tạo database
def create_database_if_not_exists():
    try:
        # Kết nối MySQL không chọn database
        connection = mysql.connector.connect(
            host=DB_HOST,
            user=DB_USER,
            password=DB_PASSWORD,
            port=DB_PORT
        )
        
        if connection.is_connected():
            cursor = connection.cursor()
            
            # Tạo database nếu chưa tồn tại
            cursor.execute(f"CREATE DATABASE IF NOT EXISTS {DB_NAME}")
            print(f"✅ Database '{DB_NAME}' đã được tạo hoặc đã tồn tại.")
            
            cursor.close()
            connection.close()
            return True
            
    except Error as e:
        print(f"❌ Lỗi kết nối MySQL: {e}")
        return False

# Cell 4: Chạy hàm kiểm tra và tạo database
success = create_database_if_not_exists()

# Cell 5: Tạo kết nối SQLAlchemy nếu database đã sẵn sàng
if success:
    try:
        # Tạo connection string
        connection_string = f'mysql+mysqlconnector://{DB_USER}:{DB_PASSWORD}@{DB_HOST}:{DB_PORT}/{DB_NAME}'
        
        # Tạo engine
        engine = create_engine(connection_string)
        
        # Kiểm tra kết nối
        with engine.connect() as connection:
            print("✅ Kết nối database thành công!")
            
    except Exception as e:
        print(f"❌ Lỗi tạo kết nối: {e}")
        engine = None

# Cell 6: Lưu dữ liệu (chạy cell này khi bạn đã có DataFrame 'data')
try:
    # Giả sử bạn đã có DataFrame tên là 'data'
    # data = pd.DataFrame(...)  # Uncomment và thêm data của bạn vào đây
    
    # Lưu từng dòng vào database
    for index, row in data.iterrows():
        try:
            # Lưu từng dòng một vào database, chế độ append để giữ lại các dòng đã lưu trước đó
            pd.DataFrame([row]).to_sql("combined_data", con=engine, if_exists="append", index=False)
            print(f"✅ Dòng {index + 1} đã được lưu thành công.")
        except Exception as e:
            print(f"❌ Lỗi khi lưu dòng {index + 1}: {e}")
    
    print("✅ Đã hoàn thành lưu tất cả các dòng!")

except NameError:
    print("⚠️ Chưa tìm thấy DataFrame 'data'. Hãy tạo DataFrame trước khi chạy cell này.")
except Exception as e:
    print(f"❌ Lỗi khi lưu dữ liệu: {e}")


✅ Database 'chat_service' đã được tạo hoặc đã tồn tại.
✅ Kết nối database thành công!
✅ Dòng 1 đã được lưu thành công.
✅ Dòng 2 đã được lưu thành công.
✅ Dòng 3 đã được lưu thành công.
✅ Dòng 4 đã được lưu thành công.
✅ Dòng 5 đã được lưu thành công.
✅ Dòng 6 đã được lưu thành công.
✅ Dòng 7 đã được lưu thành công.
✅ Dòng 8 đã được lưu thành công.
✅ Dòng 9 đã được lưu thành công.
✅ Dòng 10 đã được lưu thành công.
✅ Dòng 11 đã được lưu thành công.
✅ Dòng 12 đã được lưu thành công.
✅ Dòng 13 đã được lưu thành công.
✅ Dòng 14 đã được lưu thành công.
✅ Dòng 15 đã được lưu thành công.
✅ Dòng 16 đã được lưu thành công.
✅ Dòng 17 đã được lưu thành công.
✅ Dòng 18 đã được lưu thành công.
✅ Dòng 19 đã được lưu thành công.
✅ Dòng 20 đã được lưu thành công.
✅ Dòng 21 đã được lưu thành công.
✅ Dòng 22 đã được lưu thành công.
✅ Dòng 23 đã được lưu thành công.
✅ Dòng 24 đã được lưu thành công.
✅ Dòng 25 đã được lưu thành công.
✅ Dòng 26 đã được lưu thành công.
✅ Dòng 27 đã được lưu thành công.
✅ Dòn